## e621.net/e6ai.net JSON to `.txt` tags
----

This Python script is designed to process JSON files found within a specified directory and its subdirectories. Each JSON file is expected to contain data related to image posts, particularly sourced from online platforms such as image boards. The script parses these JSON files, extracts relevant information such as image URL, ratings, and tags, and generates caption files (`.txt`) based on this data.

Here's a breakdown of what the script does:

1. **Ignoring Tags**: The script defines a list of tags to be ignored during processing, such as "hi res", "shaded", etc.

2. **Processing Files**: The `process_file` function is responsible for processing each JSON file. It reads the JSON data, extracts the URL of the image file, determines its rating, and extracts tags associated with the image.

3. **Generating Caption File**: For each image, a caption file is generated with the same name as the image file but with a .txt extension. The rating of the image is written first, followed by processed tags.

4. **Processing Tags**: Tags are processed to replace underscores with spaces and to handle special cases such as artist tags. Ignored tags are filtered out.

In [1]:
# Define tags to be ignored using regular expressions for exact matching
ignored_tags = [r"\bblizzard entertainment\b", r"\bwarcraft\b",
    r"(?:\d{4})|(?:\d+:\d+)",
    r"\bdetailed\b", r"\bwidescreen\b", r"\b4k\b",
    r"\babsurd res\b", r"\bhi res\b", r"\bshaded\b",  r"\bdetailed\b",
    r"\btagme\b",
    r"\bdota\b",
    r"\bcreative commons\b", r"\bcc-by-nc-nd\b",
    r"\bsquare enix\b", r"\bfinal fantasy xiv\b", r"\bfinal fantasy\b",
    r"\bmythological canine\b", r"\basian mythology\b", r"\bmythological scalie\b",
    r"\bancient pokemon\b", r"\bmythological creature\b", r"\blegendary pokemon\b",
    r"\bfelis\b", r"\bfelid\b",
    r"\bsega\b",
    r"\bhasbro\b",
    r"\bzootopia\b",
    r"\bfive nights at freddy's\b",
    r"\beeveelution\b",
    r"\bdisney\b",
    r"\bmammal\b", r"\bcanis\b", r"\bcanine\b", r"\bcanid\b",
    r"\bdigimon\b", r"\bbandai namco\b",
    r"\bpokemon (species)\b",
    r"\bpal (species)\b",
    r"\bpokemon\b", r"\bnintendo\b",
    r"\\bby conditional dnp\\b",
    r"\\bconditional dnp\\b",
    r"\\bconditional_dnp\\b",
    r"\\bby\\s+conditional\\s+dnp\\b",
    r"\bgeneration\s+\d+\s+pokemon\b",
]

In [5]:
import os
import glob
import re
import json
from rich.console import Console
from rich.table import Table

console = Console()


# Function to check if a tag should be ignored based on the ignored_tags list
def should_ignore_tag(tag):
    for ignored_tag_pattern in ignored_tags:
        pattern = re.compile(ignored_tag_pattern, re.VERBOSE | re.IGNORECASE)
        if re.search(pattern, tag):
            return True
    return False


# Function to process tags and determine if they should be ignored
def process_tags(tags_dict):
    processed_tags = []
    for category, tags_list in tags_dict.items():
        category_tags = []
        if category == "artist":
            category_tags = [
                f"by {tag.replace('_', ' ').replace(' (artist)', '')}"
                for tag in tags_list
                if tag
            ]
        else:
            for tag in tags_list:
                tag = tag.replace("_", " ")
                # Escape unescaped parentheses
                tag = re.sub(r"(?<!\\)\(", r"\(", tag)
                tag = re.sub(r"(?<!\\)\)", r"\)", tag)
                if tag.lower() == "artist":
                    continue
                if not should_ignore_tag(tag):
                    category_tags.append(tag)
        processed_tags.extend(category_tags)
    return processed_tags


# Modify the process_file function to use the updated process_tags function
def process_file(file_path):
    try:
        console.print(f"Processing file: [bold]{file_path}[/bold]")
        with open(file_path, "r") as f:
            data = json.load(f)
        # Parse the URL and generate filename
        post_data = data.get("post", {})
        file_data = post_data.get("file", {})
        url = file_data.get("url")
        if url:
            filename, ext = os.path.splitext(os.path.basename(url))
            # Create caption file
            caption_file = f"{filename}.txt"
            caption_path = os.path.join(os.path.dirname(file_path), caption_file)
            with open(caption_path, "w", encoding="utf-8") as f:
                # Write rating
                rating = post_data.get("rating", "q")
                if rating == "s":
                    f.write("rating_safe, ")
                elif rating == "e":
                    f.write("rating_explicit, ")
                else:
                    f.write("rating_questionable, ")
                # Process tags
                tags_data = post_data.get("tags", {})
                processed_tags = process_tags(tags_data)
                # Check if there are any valid tags before writing
                if processed_tags:
                    # Join tags with commas and write to file
                    tags_line = ", ".join(processed_tags)
                    f.write(tags_line.strip())

                    # Create a table
                    table = Table(show_header=True, header_style="bold magenta")
                    table.add_column(caption_path, justify="center")

                    table.add_row(tags_line.strip())

                    # Print the table
                    console.print(table)
    except Exception as e:
        console.print(f"Error processing file: [bold]{file_path}[/bold]")
        console.print(e)


def recursive_process(directory):
    for file_path in glob.glob(directory + "/**/*.json", recursive=True):
        process_file(file_path)


if __name__ == "__main__":
    root_directory = r"E:\training_dir"
    #root_directory = r"C:\Users\kade\Desktop\training_dir_staging"
    recursive_process(root_directory)

Processing file: E:\training_dir\anal_beads_in_nipple\2695896.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                    E:\training_dir\anal_beads_in_nipple\80b9de3098a518295d303336422a70db.txt                    ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ 3 toes, 4 fingers, anal beads in nipple, animal genitalia, animal penis, anthro, anthrofied, areola, balls, big │
│   balls, big breasts, big butt, big penis, biped, blue eyes, bodily fluids, breasts, butt, cum, curvy figure,   │
│   equine genitalia, equine penis, erection, feet, fingers, genital fluids, genitals, gynomorph, heart symbol,   │
│ huge balls, huge breasts, huge penis, hyper, hyper balls, hyper breasts, hyper genitalia, intersex, lactating,  │
│    looking at viewer, milk, nipple fetish, nipple penetration, nipple play, nipples, nude, nude anthro, nude    │
│ gynomorph, nude intersex, open mouth, penetration, penis, sagging breasts, sex toy, sex toy in nipple, sex toy  │
│   insertion, simple background, solo, standing, tail, thick thighs, toes, voluptuous, wide hips, by sepiruth,   │
│ konami, mythology, yu-gi-oh!, blue-eyes abyss dragon, dragon, duel monster, mythological creature, mythological │
│                                scalie, scalie, digital media \(artwork\), hi res                                │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\anal_beads_in_nipple\4345729.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                    E:\training_dir\anal_beads_in_nipple\5c0f000bff95490f20757c75554c9798.txt                    ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ abdominal bulge, anal, anal beads, anal beads in nipple, anal penetration, anthro, areola, arms tied, athletic, │
│  athletic anthro, athletic female, bad end, barely visible genitalia, barely visible pussy, bdsm, big breasts,  │
│   big clitoris, black body, black fur, bodily fluids, body modification, body writing, bondage, bound, breast   │
│ expansion, breasts, breasts tied, captured, chest scar, chest tuft, clitoral hood, clitoris, countershade face, │
│ countershade torso, countershading, cross-eyed, crotch tuft, defeated, defeated heroine, degradation, drooling, │
│   ear tuft, electricity, electrocution, electrostimulation, expansion, extreme penetration, eye roll, facial    │
│ scar, fangs, female, female penetrated, fluffy, fluffy tail, forced, forced exposure, fur, game over, gameplay  │
│ mechanics, genital fluids, genital torture, genitals, glowing, glowing eyes, grey body, grey fur, hands behind  │
│   back, heart symbol, humiliation, instruction on body, lactating, large penetration, leaking, leaking milk,    │
│ leaking pussy, leg scar, leg tuft, legs tied, lightning bolt, mane, milk, multicolored body, multicolored fur,  │
│  multiple penetration, muzzle \(object\), muzzled, navel, neck tuft, nipple fetish, nipple penetration, nipple  │
│ play, nipples, object in ass, object insertion, pain, penetration, prisoner, pubes, pussy, pussy torture, rape, │
│   saliva, saliva string, scar, scars all over, sex toy, sex toy in ass, sex toy in nipple, sex toy insertion,   │
│   shaking, shocked, snout, solo, spread legs, spreading, symbol, tail, tail bondage, tail tied, tally marks,    │
│ teeth, thick thighs, torture, tremble spikes, trembling, tuft, two tone body, two tone fur, vibrator, vibrator  │
│        in nipple, western tally marks, wooden horse \(device\), word substitution, by mchoi141, blizzard        │
│ entertainment, mythology, lakaiger, mythological creature, were, werecanid, werecanine, werewolf, wolf, worgen, │
│                                               absurd res, hi res                                                │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\anal_beads_in_urethra\4024661.json

...

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                          E:\training_dir\pup_mask\bf1dfcf26208e609a73b7de10e4bf21a.txt                          ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ accessory, anal, anal penetration, animal genitalia, animal mask, animal penis, ankle cuffs, anthro, anthro on  │
│ feral, anthro penetrated, anus, balls, bestiality, big butt, black body, black fur, blue body, blue fur, blush, │
│ bodily fluids, bottomless, butt, casual sex, claws, clothed, clothing, collar, collar tag, colored nails, cuff  │
│   \(restraint\), cum, cum in ass, cum inside, cum string, dialogue, dog bed, dripping, duo, ear piercing, ear   │
│ ring, erection, feet, femboy, feral, feral penetrating, feral penetrating anthro, footprint, fur, fur markings, │
│ furniture, genital fluids, genitals, hair, hair accessory, hairband, head tuft, heart symbol, hindpaw, hoop ear │
│    ring, horn, humanoid genitalia, humanoid penis, knot, knot sitting, knotting, lamp, leaking cum, leaking     │
│     precum, living room, looking pleasured, lying, male, male/male, male penetrated, male penetrating, male     │
│ penetrating male, markings, mask, multicolored body, multicolored fur, nail file, nails, on back, onomatopoeia, │
│  open mouth, pawpads, pawprint, paws, penetration, penile, penis, pet bed, piercing, precum, precum drip, pump  │
│   \(sound effect\), pup mask, restraints, ring piercing, roleplay, sex, simple background, smile, sofa, sound   │
│ effects, submissive, tail, tattoo, teeth, text, thick thighs, tongue, tongue out, topwear, tuft, vest, whisker  │
│   markings, whiskers, white body, white fur, wide hips, womb tattoo, wrist cuffs, zipper, by wingedwilly, aki   │
│   \(wingedwilly\), doomz \(wingedwilly\), houndoom, mienshao, absurd res, digital media \(artwork\), english    │
│                                                  text, hi res                                                   │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\threaded_by_anal_beads\3704620.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                   E:\training_dir\threaded_by_anal_beads\34cb4c36b8073f91f1c907d45df68043.txt                   ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ all the way through, ambiguous threading, anal, anal beads, anal beads in ass, anal penetration, anthro, anus,  │
│ bodily fluids, breasts, butt, crouching, ejaculation, female, genital fluids, genitals, nipples, object in ass, │
│  oral, oral penetration, oral threading, penetration, pussy, sex toy, sex toy in ass, sex toy insertion, solo,  │
│  threaded by beads, threaded by object, threaded by sex toy, by heartlessangel3d, feline, meowscarada, absurd   │
│                                                   res, hi res                                                   │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir\threaded_by_sex_toy\3394922.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                    E:\training_dir\threaded_by_sex_toy\60f2e333b1d381a11ca7c1ac2e78cd60.txt                     ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│  all the way through, anal, anal masturbation, anal penetration, anal threading, anthro, balls, blush, bodily   │
│   fluids, cum, cum while penetrated, dildo, dildo sitting, erection, genital fluids, genitals, heart symbol,    │
│      hyper dildo, long dildo, looking pleasured, lube, lube in ass, lube on dildo, male, male penetrated,       │
│ masturbation, muscular, muscular male, neck bulge, nipples, object in ass, penetration, penis, sex toy, sex toy │
│  in ass, sex toy insertion, solo, thick thighs, threaded by object, threaded by sex toy, by battaph, dinayre,   │
│                                                  wolf, hi res                                                   │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

## Delete every JSON file ⚠️

---

In [6]:
import glob
import os

def delete_json_files(directory):
    # Create the path pattern to match JSON files
    pattern = os.path.join(directory, '**', '*.json')
    
    # Find all JSON files using glob
    json_files = glob.glob(pattern, recursive=True)
    
    # Delete each JSON file
    for file_path in json_files:
        try:
            os.remove(file_path)
            print(f"Deleted: {file_path}")
        except OSError as e:
            print(f"Error deleting {file_path}: {e}")

if __name__ == "__main__":
    # Specify the directory path
    directory_path = r'E:\training_dir'
    
    # Call the function to delete JSON files recursively
    delete_json_files(directory_path)

Deleted: E:\training_dir\anal_beads_in_nipple\2695896.json
Deleted: E:\training_dir\anal_beads_in_nipple\4345729.json
Deleted: E:\training_dir\anal_beads_in_urethra\4024661.json
Deleted: E:\training_dir\big_power_bottom\3906412.json
Deleted: E:\training_dir\by_jay_naylor\210825.json
Deleted: E:\training_dir\by_jay_naylor\2734058.json
Deleted: E:\training_dir\by_jay_naylor\2802402.json
Deleted: E:\training_dir\by_jay_naylor\2833520.json
Deleted: E:\training_dir\by_jay_naylor\2878273.json
Deleted: E:\training_dir\by_jay_naylor\3229750.json
Deleted: E:\training_dir\by_jay_naylor\3653027.json
Deleted: E:\training_dir\by_jay_naylor\4599450.json
Deleted: E:\training_dir\by_jay_naylor\623980.json
Deleted: E:\training_dir\pup_mask\1591509.json
Deleted: E:\training_dir\pup_mask\1801624.json
Deleted: E:\training_dir\pup_mask\1828587.json
Deleted: E:\training_dir\pup_mask\1852247.json
Deleted: E:\training_dir\pup_mask\2072090.json
Deleted: E:\training_dir\pup_mask\2196453.json
Deleted: E:\trainin